this notebook is designed to train lda models to classify events from text preprocessing to comparing different lda models and choosing the best model.

In [1]:
from pymystem3 import Mystem
my_stem = Mystem()

import nltk
import logging

try:
    nltk.corpus.stopwords.words('english')
except:
    nltk.download('stopwords')

import pandas as pd
from collections import defaultdict

import gensim.models

MODEL_NAME = 'lda'
DATA_PATH = '/data/'
EVENTS_PATH = f'{DATA_PATH}events/'
RAW_PATH = f'/{EVENTS_PATH}/raw/'
DOCS_PATH = f'/{EVENTS_PATH}/lda/'
MODEL_PATH = f'{DATA_PATH}models/{MODEL_NAME}/' 
TMP_PATH = f'{DATA_PATH}tmp/{MODEL_NAME}/'

logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)

samples = range(5, 102) # number of topics for lda models

text preprocessing:
<ol>
    <li>lowercasing </li>
    <li>removing all non alphanum symbols </li>
    <li>removing all numbers </li>
    <li>lemmetazing of text </li>
    <li>removing useless space symbols </li>
</ol>

In [ ]:
from nltk.corpus import stopwords
from gensim.parsing.preprocessing import strip_multiple_whitespaces
from gensim.parsing.preprocessing import strip_non_alphanum


useless_symbols = set(['_', 'ー'])
filter_words = set()
# load stopwords from nltk
filter_words = filter_words.union(set(stopwords.words('english')))
filter_words = filter_words.union(set(stopwords.words('russian')))
# load own stopwords
with open('stopwords_full.txt') as f:
    filter_words = filter_words.union(set([word for line in f for word in line.split()]))


# input: document: str
# output: document: str
# make preprocessing of documents, remove useless symbols, remove useless words
def preprocessor(s: str):
    # all letter to lower case
    s = s.lower() 
    
    # remove all symbol, which aren't letter or num
    s = strip_non_alphanum(s)
    # strip_non_alphanum don't remove '_' symbol
    s = ''.join(map(lambda c: ' ' if c in useless_symbols else c, s))

    s = ''.join(my_stem.lemmatize(s))
    # replace all space symbol like space, tab, \n to simple space and remove double and for space
    s = strip_multiple_whitespaces(s)
    # remove empty words and words from filtered words 
    s = ' '.join(list(filter(lambda w:  len(w) > 0 and not (w in filter_words or w.isdigit()), s.split(' '))))
    return s


# load file and drop documents with empty text
df = pd.concat([pd.read_csv(RAW_PATH + 'spb_events.csv'), pd.read_csv(RAW_PATH + 'moscow_events.csv')])
#df = pd.read_csv(RAW_PATH + 'spb_events.csv')

# preprocess of corpus
df['description'] = df['captions'].apply(preprocessor)

# save results
!mkdir {DOCS_PATH}/events_lda
df.to_csv(r'' + DOCS_PATH + 'events_norm.csv', index=False)

<ul>
    <li>filtering stopwords</li>
    <li>generation bigrams and trigrams </li>
    <li>generation dictionary and corpus for training</li>
</ul>
Note: stopwords are combining various particles, prepositions of conjunctions and other words that have little meaning in this task and contextual stop words - words with a high level of overlap in different topics ('спб', 'love', 'likes4likes'). Сontextual stopwords were obtained after several training cycles and filtering useless words. 
<br><br>
Note: this code must be executed after restarting the notebook 

In [17]:
from gensim.models import Phrases
from gensim.corpora import Dictionary

with open('../stopwords/stopwords_context.txt') as f:
    filter_words = set([word for line in f for word in line.split()])


df = pd.read_csv(DOCS_PATH + 'events_norm.csv').dropna()
df['description'] = df['description'].apply(lambda s: ' '.join(list(filter(lambda w: not (w in filter_words), s.split(' ')))))
docs = list(map(lambda s: s.split(), df['description'].tolist()))

bigram = Phrases(docs, min_count=5)
trigram = Phrases(bigram[docs])  

for idx in range(len(docs)):
    for token in trigram[bigram[docs[idx]]]:
        if '_' in token:
            # Token is a bigram, add to document.
            docs[idx].append(token)
            
dictionary = Dictionary(docs)

# Filter out words that occur less than 20 documents, or more than 10% of the documents.
dictionary.filter_extremes(no_below=20, no_above=0.1)
# Bag-of-words representation of the documents.
corpus = [dictionary.doc2bow(doc) for doc in docs]
temp = dictionary[0] # it needed for working of lda training

2020-07-16 14:31:22,875 : INFO : collecting all words and their counts
2020-07-16 14:31:22,877 : INFO : PROGRESS: at sentence #0, processed 0 words and 0 word types
2020-07-16 14:31:29,524 : INFO : PROGRESS: at sentence #10000, processed 3713347 words and 2697503 word types
2020-07-16 14:31:30,364 : INFO : collected 2938062 word types from a corpus of 4105782 words (unigram + bigrams) and 10214 sentences
2020-07-16 14:31:30,365 : INFO : using 2938062 counts as vocab in Phrases<0 vocab, min_count=5, threshold=10.0, max_vocab_size=40000000>
2020-07-16 14:31:30,366 : INFO : collecting all words and their counts
2020-07-16 14:31:30,367 : INFO : PROGRESS: at sentence #0, processed 0 words and 0 word types
2020-07-16 14:31:49,296 : INFO : PROGRESS: at sentence #10000, processed 3173219 words and 2857562 word types
2020-07-16 14:31:51,341 : INFO : collected 3114433 word types from a corpus of 3510642 words (unigram + bigrams) and 10214 sentences
2020-07-16 14:31:51,342 : INFO : using 3114433 

training list of models. Samples - different number of topics. For each sample is trained one lda model.

In [ ]:
from gensim.models import LdaMulticore

model_list = []
samples = range(5, 102)
!mkdir {MODEL_PATH}

for n_topics in samples:
    path = f'{MODEL_PATH}{n_topics}/'
    !mkdir {path}
    
    chunksize = len(df)
    passes = 10
    iterations = 100

    model = LdaMulticore(
        workers=35,
        corpus=corpus,
        id2word=dictionary.id2token,
        chunksize=chunksize,
        eta='auto',
        iterations=iterations,
        num_topics=n_topics,
        passes=passes,
        eval_every=None
    )
    model.save(path + "mdl")
    model_list.append(model)

if models exist and are trained, we can load them

In [2]:
from gensim.models import LdaMulticore

model_list = []

for n_topics in samples:
    path = f'{MODEL_PATH}{n_topics}/mdl'
    model_list.append(LdaMulticore.load(path))


2020-07-17 09:51:19,333 : INFO : loading LdaMulticore object from /data/models/lda/5/mdl
2020-07-17 09:51:19,335 : INFO : loading expElogbeta from /data/models/lda/5/mdl.expElogbeta.npy with mmap=None
2020-07-17 09:51:19,337 : INFO : setting ignored attribute dispatcher to None
2020-07-17 09:51:19,337 : INFO : setting ignored attribute id2word to None
2020-07-17 09:51:19,338 : INFO : setting ignored attribute state to None
2020-07-17 09:51:19,338 : INFO : loaded /data/models/lda/5/mdl
2020-07-17 09:51:19,338 : INFO : loading LdaState object from /data/models/lda/5/mdl.state
2020-07-17 09:51:19,342 : INFO : loaded /data/models/lda/5/mdl.state
2020-07-17 09:51:19,349 : INFO : loading LdaMulticore object from /data/models/lda/6/mdl
2020-07-17 09:51:19,351 : INFO : loading expElogbeta from /data/models/lda/6/mdl.expElogbeta.npy with mmap=None
2020-07-17 09:51:19,352 : INFO : setting ignored attribute dispatcher to None
2020-07-17 09:51:19,352 : INFO : setting ignored attribute id2word to N

2020-07-17 09:51:19,541 : INFO : loaded /data/models/lda/17/mdl
2020-07-17 09:51:19,542 : INFO : loading LdaState object from /data/models/lda/17/mdl.state
2020-07-17 09:51:19,551 : INFO : loaded /data/models/lda/17/mdl.state
2020-07-17 09:51:19,557 : INFO : loading LdaMulticore object from /data/models/lda/18/mdl
2020-07-17 09:51:19,559 : INFO : loading expElogbeta from /data/models/lda/18/mdl.expElogbeta.npy with mmap=None
2020-07-17 09:51:19,560 : INFO : setting ignored attribute dispatcher to None
2020-07-17 09:51:19,561 : INFO : setting ignored attribute id2word to None
2020-07-17 09:51:19,561 : INFO : setting ignored attribute state to None
2020-07-17 09:51:19,561 : INFO : loaded /data/models/lda/18/mdl
2020-07-17 09:51:19,562 : INFO : loading LdaState object from /data/models/lda/18/mdl.state
2020-07-17 09:51:19,571 : INFO : loaded /data/models/lda/18/mdl.state
2020-07-17 09:51:19,578 : INFO : loading LdaMulticore object from /data/models/lda/19/mdl
2020-07-17 09:51:19,579 : INF

2020-07-17 09:51:19,849 : INFO : setting ignored attribute dispatcher to None
2020-07-17 09:51:19,849 : INFO : setting ignored attribute id2word to None
2020-07-17 09:51:19,849 : INFO : setting ignored attribute state to None
2020-07-17 09:51:19,850 : INFO : loaded /data/models/lda/30/mdl
2020-07-17 09:51:19,850 : INFO : loading LdaState object from /data/models/lda/30/mdl.state
2020-07-17 09:51:19,867 : INFO : loaded /data/models/lda/30/mdl.state
2020-07-17 09:51:19,873 : INFO : loading LdaMulticore object from /data/models/lda/31/mdl
2020-07-17 09:51:19,874 : INFO : loading expElogbeta from /data/models/lda/31/mdl.expElogbeta.npy with mmap=None
2020-07-17 09:51:19,877 : INFO : setting ignored attribute dispatcher to None
2020-07-17 09:51:19,877 : INFO : setting ignored attribute id2word to None
2020-07-17 09:51:19,877 : INFO : setting ignored attribute state to None
2020-07-17 09:51:19,878 : INFO : loaded /data/models/lda/31/mdl
2020-07-17 09:51:19,878 : INFO : loading LdaState objec

2020-07-17 09:51:20,237 : INFO : loaded /data/models/lda/42/mdl.state
2020-07-17 09:51:20,243 : INFO : loading LdaMulticore object from /data/models/lda/43/mdl
2020-07-17 09:51:20,245 : INFO : loading expElogbeta from /data/models/lda/43/mdl.expElogbeta.npy with mmap=None
2020-07-17 09:51:20,247 : INFO : setting ignored attribute dispatcher to None
2020-07-17 09:51:20,247 : INFO : setting ignored attribute id2word to None
2020-07-17 09:51:20,248 : INFO : setting ignored attribute state to None
2020-07-17 09:51:20,248 : INFO : loaded /data/models/lda/43/mdl
2020-07-17 09:51:20,248 : INFO : loading LdaState object from /data/models/lda/43/mdl.state
2020-07-17 09:51:20,271 : INFO : loaded /data/models/lda/43/mdl.state
2020-07-17 09:51:20,278 : INFO : loading LdaMulticore object from /data/models/lda/44/mdl
2020-07-17 09:51:20,279 : INFO : loading expElogbeta from /data/models/lda/44/mdl.expElogbeta.npy with mmap=None
2020-07-17 09:51:20,281 : INFO : setting ignored attribute dispatcher to

2020-07-17 09:51:20,691 : INFO : setting ignored attribute id2word to None
2020-07-17 09:51:20,691 : INFO : setting ignored attribute state to None
2020-07-17 09:51:20,692 : INFO : loaded /data/models/lda/55/mdl
2020-07-17 09:51:20,692 : INFO : loading LdaState object from /data/models/lda/55/mdl.state
2020-07-17 09:51:20,721 : INFO : loaded /data/models/lda/55/mdl.state
2020-07-17 09:51:20,727 : INFO : loading LdaMulticore object from /data/models/lda/56/mdl
2020-07-17 09:51:20,729 : INFO : loading expElogbeta from /data/models/lda/56/mdl.expElogbeta.npy with mmap=None
2020-07-17 09:51:20,731 : INFO : setting ignored attribute dispatcher to None
2020-07-17 09:51:20,732 : INFO : setting ignored attribute id2word to None
2020-07-17 09:51:20,732 : INFO : setting ignored attribute state to None
2020-07-17 09:51:20,732 : INFO : loaded /data/models/lda/56/mdl
2020-07-17 09:51:20,733 : INFO : loading LdaState object from /data/models/lda/56/mdl.state
2020-07-17 09:51:20,761 : INFO : loaded /

2020-07-17 09:51:21,250 : INFO : loading LdaMulticore object from /data/models/lda/68/mdl
2020-07-17 09:51:21,252 : INFO : loading expElogbeta from /data/models/lda/68/mdl.expElogbeta.npy with mmap=None
2020-07-17 09:51:21,255 : INFO : setting ignored attribute dispatcher to None
2020-07-17 09:51:21,256 : INFO : setting ignored attribute id2word to None
2020-07-17 09:51:21,256 : INFO : setting ignored attribute state to None
2020-07-17 09:51:21,256 : INFO : loaded /data/models/lda/68/mdl
2020-07-17 09:51:21,257 : INFO : loading LdaState object from /data/models/lda/68/mdl.state
2020-07-17 09:51:21,292 : INFO : loaded /data/models/lda/68/mdl.state
2020-07-17 09:51:21,299 : INFO : loading LdaMulticore object from /data/models/lda/69/mdl
2020-07-17 09:51:21,300 : INFO : loading expElogbeta from /data/models/lda/69/mdl.expElogbeta.npy with mmap=None
2020-07-17 09:51:21,303 : INFO : setting ignored attribute dispatcher to None
2020-07-17 09:51:21,303 : INFO : setting ignored attribute id2wo

2020-07-17 09:51:21,851 : INFO : setting ignored attribute state to None
2020-07-17 09:51:21,852 : INFO : loaded /data/models/lda/80/mdl
2020-07-17 09:51:21,852 : INFO : loading LdaState object from /data/models/lda/80/mdl.state
2020-07-17 09:51:21,892 : INFO : loaded /data/models/lda/80/mdl.state
2020-07-17 09:51:21,899 : INFO : loading LdaMulticore object from /data/models/lda/81/mdl
2020-07-17 09:51:21,900 : INFO : loading expElogbeta from /data/models/lda/81/mdl.expElogbeta.npy with mmap=None
2020-07-17 09:51:21,903 : INFO : setting ignored attribute dispatcher to None
2020-07-17 09:51:21,904 : INFO : setting ignored attribute id2word to None
2020-07-17 09:51:21,904 : INFO : setting ignored attribute state to None
2020-07-17 09:51:21,904 : INFO : loaded /data/models/lda/81/mdl
2020-07-17 09:51:21,905 : INFO : loading LdaState object from /data/models/lda/81/mdl.state
2020-07-17 09:51:21,945 : INFO : loaded /data/models/lda/81/mdl.state
2020-07-17 09:51:21,952 : INFO : loading LdaMu

2020-07-17 09:51:22,571 : INFO : loading expElogbeta from /data/models/lda/93/mdl.expElogbeta.npy with mmap=None
2020-07-17 09:51:22,574 : INFO : setting ignored attribute dispatcher to None
2020-07-17 09:51:22,575 : INFO : setting ignored attribute id2word to None
2020-07-17 09:51:22,575 : INFO : setting ignored attribute state to None
2020-07-17 09:51:22,575 : INFO : loaded /data/models/lda/93/mdl
2020-07-17 09:51:22,576 : INFO : loading LdaState object from /data/models/lda/93/mdl.state
2020-07-17 09:51:22,621 : INFO : loaded /data/models/lda/93/mdl.state
2020-07-17 09:51:22,627 : INFO : loading LdaMulticore object from /data/models/lda/94/mdl
2020-07-17 09:51:22,629 : INFO : loading expElogbeta from /data/models/lda/94/mdl.expElogbeta.npy with mmap=None
2020-07-17 09:51:22,632 : INFO : setting ignored attribute dispatcher to None
2020-07-17 09:51:22,633 : INFO : setting ignored attribute id2word to None
2020-07-17 09:51:22,633 : INFO : setting ignored attribute state to None
2020-0

calculating Coherence score for evaluating quality of lda models and choosing the best model

In [33]:
from gensim.models import CoherenceModel

def compute_coherence_values(dictionary, texts, models):
    coherence_values = []
    for model in models:
        coherencemodel = CoherenceModel(model=model, texts=texts, dictionary=dictionary, coherence='c_v')
        coherence_values.append(coherencemodel.get_coherence())
    return coherence_values

coherence_values = compute_coherence_values(dictionary, docs, model_list)

In [31]:
import plotly.graph_objects as go

x = list(map(lambda m: m.num_topics, model_list))
ind = list(range(len(df_scores)))

fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=df_scores['coherence'], name='coherence', text=ind))

fig.show()

defining functions and varriables for evaluating pairbased f-score for lda models

In [38]:
df_cross = pd.read_csv('../cross_valid_union.csv')
lname = {'positive': 2, 'negative': 1}

def prepare_labels(model, df, corpus):
    #print(len(df), len(corpus))
    events = []
    for doc_ind in range(len(corpus)):
        topics = model.get_document_topics(corpus[doc_ind])
        best_topic = 0
        for topic_ind in range(len(topics)):
            if topics[best_topic][1] < topics[topic_ind][1]:
                best_topic = topic_ind
        if len(topics) == 0:
            events.append((df.iloc[doc_ind]['id'], -1))
        else:
            events.append((df.iloc[doc_ind]['id'], topics[best_topic][0]))
    return events

def evaluate_score(events):
    tp, tn, fp, fn = 0, 0, 0, 0
    d = {}
    for event, l in events:
        d[event] = l
    
    for _, row in df_cross.iterrows():
        a = row['id_a']
        b = row['id_b']
        l = row['label']
        
        tp += 1 if d[a] == d[b] and l == lname['positive'] else 0
        tn += 1 if d[a] != d[b] and l == lname['negative'] else 0
        fp += 1 if d[a] == d[b] and l == lname['negative'] else 0
        fn += 1 if d[a] != d[b] and l == lname['positive'] else 0
    
    precision = tp / (tp + fp)
    recall = tp / (tp + fn)
    f1 = 2 * precision * recall / (precision + recall)    
    rand = (tp + tn) / (tp + tn + fp + fn)
    return [precision, recall, f1, rand, tp, tn, fp, fn]

evaluating f-score

In [39]:
import pandas as pd
scores = []

for ind, model in enumerate(model_list):
    events = prepare_labels(model, df, corpus)
    score = evaluate_score(events)
    scores.append([model.num_topics] + score)
    
df_scores = pd.DataFrame(scores, columns = ['n_topics', 'precision', 'recall', 'f1', 'rand', 'tp', 'tn', 'fp', 'fn'])

In [40]:
df_scores['coherence'] = coherence_values

In [49]:
!mkdir {TMP_PATH}
df_scores.to_csv(r'' + TMP_PATH + 'scores.csv')

mkdir: cannot create directory ‘/data/tmp/lda/’: File exists


In [3]:
df_scores = pd.read_csv(TMP_PATH + 'scores.csv')

finging the best model

In [4]:
best_score = df_scores.iloc[df_scores['f1'].idxmax()]
#best = (best_score['f1'], best_score['n_topics'])
best = (best_score['f1'], best_score['n_topics'])
best

(0.6187961985216472, 14.0)

In [6]:
def find_best_by(param_name: str):
    best_score = df_scores.iloc[df_scores[param_name].idxmax()]
    return (best_score[param_name], best_score['n_topics'])

In [7]:
find_best_by('f1')

(0.6187961985216472, 14.0)

In [8]:
find_best_by('coherence')

(0.5844902736327479, 101.0)

plotting metrics for models

In [15]:
import plotly.graph_objects as go

x = df_scores['n_topics']
fig = go.Figure()
fig.add_trace(go.Scatter(x=x, y=df_scores['precision'], name='precision'))
fig.add_trace(go.Scatter(x=x, y=df_scores['recall'], name='recall'))
fig.add_trace(go.Scatter(x=x, y=df_scores['f1'], name='f1'))

fig.update_layout(
    autosize=False,
    width=800,
    height=500
)
fig.show()

fig2 = go.Figure()
fig2.add_trace(go.Scatter(x=x, y=df_scores['coherence'], name='coherence'))

fig2.update_layout(
    autosize=False,
    width=800,
    height=500
)
fig2.show()


function for drawing a lda model

In [15]:
from pyLDAvis import gensim as gensim_lda
import pyLDAvis

def plot_lda(num_topics):
    ind = list(map(lambda m: m.num_topics, model_list)).index(num_topics)
    pyLDAvis.enable_notebook()
    return gensim_lda.prepare(model_list[ind], corpus, dictionary)

In [19]:
plot_lda(66)

2020-07-16 14:33:09,749 : INFO : Note: NumExpr detected 40 cores but "NUMEXPR_MAX_THREADS" not set, so enforcing safe limit of 8.
2020-07-16 14:33:09,751 : INFO : NumExpr defaulting to 8 threads.
/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:257: FutureWarning:

Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.




PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
37     0.119120  0.041779       1        1  24.792486
19     0.141691  0.043013       2        1   8.967405
9      0.164142  0.021093       3        1   8.959176
25     0.135126  0.056443       4        1   3.929952
31    -0.190503  0.066241       5        1   3.583862
...         ...       ...     ...      ...        ...
0      0.023983 -0.009888      62        1   0.292646
59     0.075254  0.026888      63        1   0.289472
6      0.013425  0.023375      64        1   0.250648
2     -0.035099  0.032813      65        1   0.225230
26     0.089382  0.015037      66        1   0.214685

[66 rows x 5 columns], topic_info=      Category          Freq      Term         Total  loglift  logprob
10585  Default  11754.000000     пасха  11754.000000  30.0000  30.0000
13418  Default   3261.000000    vkfest   3261.000000  29.0000  29.0000
2491   Default   4195.000000     зенит   4195.000000  28.0000  28.0000
3091   Default   3284.000000    футбол   3284.000000  27.0000  27.0000
13643  Default   2130.000000   vkfest5   2130.000000  26.0000  26.0000
...        ...           ...       ...           ...      ...      ...
1444   Topic66     16.622572  внимание   1750.066284   1.4871  -5.9458
3122   Topic66     17.003124   магазин   2337.459229   1.2203  -5.9232
8987   Topic66     17.525984      яйцо   3365.378906   0.8861  -5.8929
1321   Topic66     15.650694        np   1293.665161   1.7290  -6.0061
551    Topic66     15.354589    ссылка   2302.271240   1.1335  -6.0252

[3546 rows x 6 columns], token_table=       Topic      Freq  Term
term                        
12085      1  0.055245  10км
12085     12  0.027623  10км
12085     30  0.856303  10км
12085     43  0.027623  10км
18409      1  0.414527   11н
...      ...       ...   ...
11121     52  0.001197     ᅠ
11121     53  0.043091     ᅠ
11121     58  0.001197     ᅠ
11121     60  0.001197     ᅠ
11121     64  0.001197     ᅠ

[42469 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[38, 20, 10, 26, 32, 56, 45, 49, 51, 43, 37, 19, 53, 4, 9, 14, 62, 31, 50, 24, 42, 8, 55, 36, 58, 12, 41, 6, 18, 63, 17, 23, 65, 40, 16, 61, 44, 57, 13, 35, 64, 46, 52, 11, 34, 15, 28, 30, 25, 48, 47, 66, 39, 29, 54, 2, 21, 33, 22, 5, 59, 1, 60, 7, 3, 27])

In [32]:
plot_lda(24)

/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:257: FutureWarning:

Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.




PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
20     0.104110  0.021922       1        1  37.110157
13     0.106192  0.046654       2        1  12.476357
4      0.106761  0.029445       3        1   5.546432
18    -0.025445  0.035327       4        1   4.432842
6     -0.084259  0.069103       5        1   4.048577
19    -0.080457  0.061977       6        1   3.985420
0     -0.032898  0.060581       7        1   3.954316
17    -0.233231 -0.177370       8        1   3.154387
11     0.228778 -0.349636       9        1   3.109341
7      0.006868  0.064389      10        1   2.634294
2      0.008836  0.044060      11        1   2.395024
5      0.012305 -0.026515      12        1   2.068512
12     0.057364  0.047795      13        1   1.792730
16     0.098195  0.031011      14        1   1.683776
8      0.016047  0.061755      15        1   1.616352
21     0.094511  0.041593      16        1   1.424849
22    -0.044377  0.060013      17        1   1.303069
9     -0.108630 -0.074015      18        1   1.252741
23    -0.034165  0.060670      19        1   1.252156
15    -0.182378 -0.047069      20        1   1.241603
10    -0.063470 -0.065021      21        1   1.033498
14     0.079879  0.038673      22        1   0.958091
3     -0.131488 -0.065353      23        1   0.909430
1      0.100950  0.030010      24        1   0.616057, topic_info=      Category          Freq      Term         Total  loglift  logprob
10585  Default  11433.000000     пасха  11433.000000  30.0000  30.0000
2491   Default   4126.000000     зенит   4126.000000  29.0000  29.0000
5358   Default   5956.000000     маска   5956.000000  28.0000  28.0000
13418  Default   3153.000000    vkfest   3153.000000  27.0000  27.0000
3042   Default   2673.000000   спартак   2673.000000  26.0000  26.0000
...        ...           ...       ...           ...      ...      ...
2505   Topic24     42.146969       bmw    580.944153   2.4661  -6.0695
85     Topic24     43.088055  рождение   1462.872192   1.5647  -6.0475
2634   Topic24     43.295856     фильм   2213.489014   1.1553  -6.0427
1475   Topic24     41.826168      тело   1904.911133   1.2709  -6.0772
1444   Topic24     41.534912  внимание   1751.127319   1.3481  -6.0842

[1488 rows x 6 columns], token_table=       Topic      Freq       Term
term                             
19078     10  0.978195   12апреля
19078     16  0.005590   12апреля
6100       2  0.016208  14февраля
6100       3  0.016208  14февраля
6100       7  0.008104  14февраля
...      ...       ...        ...
11121     13  0.009079          ᅠ
11121     15  0.001135          ᅠ
11121     16  0.003405          ᅠ
11121     19  0.010214          ᅠ
11121     22  0.001135          ᅠ

[10600 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[21, 14, 5, 19, 7, 20, 1, 18, 12, 8, 3, 6, 13, 17, 9, 22, 23, 10, 24, 16, 11, 15, 4, 2])

In [21]:
plot_lda(14)

/opt/conda/lib/python3.7/site-packages/pyLDAvis/_prepare.py:257: FutureWarning:

Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.




PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
2     -0.088895 -0.054072       1        1  44.402313
10    -0.030585 -0.048357       2        1   6.601017
0     -0.072983 -0.073916       3        1   6.509389
7     -0.119342 -0.068978       4        1   5.563582
11     0.142337  0.280394       5        1   4.971577
12     0.155049  0.051878       6        1   4.149778
8      0.112654 -0.002322       7        1   3.880979
6      0.031606 -0.044014       8        1   3.735856
9      0.050708 -0.063653       9        1   3.712287
1      0.070031 -0.035367      10        1   3.659381
5      0.062796 -0.035180      11        1   3.562701
3     -0.317667  0.185548      12        1   3.307796
13     0.062249 -0.038996      13        1   3.290727
4     -0.057956 -0.052964      14        1   2.652607, topic_info=      Category          Freq      Term         Total  loglift  logprob
10585  Default  11040.000000     пасха  11040.000000  30.0000  30.0000
2491   Default   4199.000000     зенит   4199.000000  29.0000  29.0000
5358   Default   6061.000000     маска   6061.000000  28.0000  28.0000
13418  Default   2949.000000    vkfest   2949.000000  27.0000  27.0000
3091   Default   3301.000000    футбол   3301.000000  26.0000  26.0000
...        ...           ...       ...           ...      ...      ...
879    Topic14    187.768677      кожа   2865.958984   0.9042  -6.0355
8037   Topic14    173.772034     обувь   1405.513184   1.5392  -6.1130
5427   Topic14    165.685623   продажа   1003.262512   1.8287  -6.1606
1978   Topic14    166.135056  followme   1331.171387   1.5486  -6.1579
199    Topic14    165.545258     номер   1331.677246   1.5447  -6.1615

[955 rows x 6 columns], token_table=       Topic      Freq        Term
term                              
20101      4  0.018515  101kruzhka
20101      9  0.962784  101kruzhka
19078      1  0.014499    12апреля
19078      4  0.007249    12апреля
19078      7  0.007249    12апреля
...      ...       ...         ...
11121      7  0.718250           ᅠ
11121      8  0.016511           ᅠ
11121     11  0.001179           ᅠ
11121     12  0.001179           ᅠ
11121     14  0.005897           ᅠ

[5368 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[3, 11, 1, 8, 12, 13, 9, 7, 10, 2, 6, 4, 14, 5])

In [36]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:50% !important; }</style>"))
